### This Notebook will use a formula to determine the reccomended KVA for a transformer when it is replaced
The formula uses customer count and customer consumption history downsteam of each transformer. When Electric Trouble Crews replace a transformer the reccomended size will available when an Engineer is not (for example after hours or weekends). This will help ensure the right size transformer is used based on consumption history, and not merley just areplacement that could be under-sized or over-sized.
The second half of the Notebook explores the electric consumption data with a [SpatialDataFrame](https://esri.github.io/arcgis-python-api/apidoc/html/arcgis.features.toc.html?highlight=spatialdataframe#spatialdataframe) using the customers table modifed in the first half.


In [1]:
import arcpy
#import numpy
#import pandas as pd
from datetime import datetime

In [2]:
gdb = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb"
txSource = r"C:\GISData\Data\Snapshot\mxElectric.geodatabase\Electric\main.eTransformerBank"
txDest = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank"
svcPntDest = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eServicePoint"
custAcctSource = r"C:\GISData\Data\Snapshot\mxElectric.geodatabase\main.eCUSTOMERACCOUNT"
custAcctDest = r"C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\eCUSTOMERACCOUNT"
txAddFlds = ["kWDSum","CF","kWDSumXCF","kWDSumXCF_A","kWDSumXCF_B","kWDSumXCF_C"]
txFlds = ["OID@","GLOBALID","kWDSum","CF","kWDSumXCF","CUSTOMERCOUNT","MAXCUSTOMERCONSUMPTION_A","MAXCUSTOMERCONSUMPTION_B","MAXCUSTOMERCONSUMPTION_C","DEVICEID","FEEDERID","FEEDERID2","INSTALLATIONDATE","PHASEDESIGNATION","SUBTYPE","RATEDKVA_A","RATEDKVA_B","RATEDKVA_C","STRUCTUREID","FACILITYID","AVGCUSTOMERCONSUMPTION_A","AVGCUSTOMERCONSUMPTION_B","AVGCUSTOMERCONSUMPTION_C","PURPOSE","STREETADDRESS","eSupportStructure_GlobalID","eSurfaceStructure_GlobalID"]
svcPntFlds = ["OID@","GLOBALID","eTransformerBank_GLOBALID","FEEDERID","PHASEDESIGNATION","SUBTYPE","CUSTOMERCOUNT","AVGCUSTOMERCONSUMPTION","MAXCUSTOMERCONSUMPTION","STREETADDRESS","eSupportStructure_GLOBALID"]
custAcctFlds = ["eServicePoint_GlobalID","MAXCONSUMPTION"]

- For each customer downstream of a transformer, obtain Estimated Demand using summer or winter demand table, translate kwH (key) to kwD (vale). 
- Sum the kwD 
- Using coincidence factor dictionary, number of customers downstream of transformer (key) to obtain coincidence factor (value). - Multiply coincidence factor by sum of kwD
- Result is minimum kvA transformer
 
After running Accumulate Upstream (seperate C# program run against GIS that traces geometric network) the number of customers and consumption is available on each transformer. Obtain CF using number of customers on transformer, convert maxconsumption to kwD. Multiply kwD by CF. Result is minimum kvA transformer.

In [3]:
if datetime.today().month >= 5 <= 9:
    #print("Using Summer Peak")
    summerPeak = True
    estimatedDemand = {50:2.40,100:2.67,150:2.94,200:3.20,250:3.46,300:3.72,350:3.98,400:4.23,450:4.48,500:4.73,550:4.97,600:5.21,
                    650:5.45,700:5.68,750:5.92,800:6.15,850:6.37,900:6.60,950:6.82,1000:7.03,1050:7.25,1100:7.46,1150:7.67,
                    1200:7.88,1250:8.08,1300:8.28,1350:8.48,1400:8.67,1450:8.86,1500:9.05,1550:9.24,1600:9.42,1650:9.60,
                    1700:9.78,1750:9.95,1800:10.12,1850:10.29,1900:10.46,1950:10.62,2000:10.78,2050:10.94,2100:11.10,2150:11.26,
                    2200:11.41,2250:11.57,2300:11.73,2350:11.89,2400:12.05,2450:12.21,2500:2.36,2550:2.52,2600:12.68,2650:12.84,
                    2700:13.00,2750:13.16,2800:13.31,2850:13.47,2900:13.63,2950:13.79,3000:13.95}
else:
    #print("Using Winter Peak")
    winterPeak = True
    estimatedDemand = {50:1.97,100:2.33,150:2.69,200:3.05,250:3.41,300:3.76,350:4.11,400:4.45,450:4.80,500:5.14,550:5.48,
                       600:5.82,650:6.15,700:6.49,750:6.82,800:7.14,850:7.47,900:7.79,950:8.11,1000:8.43,1050:8.74,1100:9.05,
                       1150:9.36,1200:9.67,1250:9.97,1300:10.27,1350:10.57,1400:10.87,1450:11.16,1500:11.45,1550:11.74,1600:12.03,
                       1650:12.31,1700:12.60,1750:12.87,1800:13.15,1850:13.42,1900:13.70,1950:13.96,2000:14.23,2050:14.45,
                       2100:14.68,2150:14.90,2200:15.13,2250:15.35,2300:15.58,2350:15.80,2400:16.03,2450:16.25,2500:16.48,
                       2550:16.70,2600:16.93,2650:17.15,2700:17.38,2750:17.60,2800:17.83,2850:18.05,2900:18.28,2950:18.50,
                       3000:18.73}

# coincidence factor
cf = {1:1.0,2:0.85,3:0.74,4:0.66,5:0.61,6:0.57,7:0.54,8:0.52,9:0.5,10:0.49,11:0.47,12:0.46,13:0.45,14:0.43,15:0.42,16:0.41,
      17:0.39,18:0.38,19:0.38,20:0.37}


In [4]:
arcpy.env.workspace = gdb
arcpy.env.overwriteOutput = True

In [46]:
def sumSvcPnts(_OID,_GID):
    kwhConsumption = 0
    customerCount = 0
    kwdConsumption = 0
    cf = 0
    kva = 0
    svcGUID = []
    meterConsumption = []
    customers = []
    kwdCon = []
    custCountGUID = 0
    svcPntCount = 0
    svcSum = 0
    nl = '\n'
    t = '\t'
    # create a list of all service points related to transformer
    with arcpy.da.SearchCursor(svcPntDest,svcPntFlds,f"eTransformerBank_GLOBALID = '{_GID}'") as svcPnts:
        for svcPnt in svcPnts:
            #print(f'Found svcPnt GUID {svcPnt[1]} related to eTransformerBank_GLOBALID = {svcPnt[2]}')
            svcGUID.append(svcPnt[1])
    svcPntCount = len(svcGUID)
    #print(svcPntCount)
    #for each service point related to the transformer find the related customer consumption
    for guid in svcGUID:
        kwhConsumption,customerCount,kwdConsumption = getConsumption(guid)
        meterConsumption.append(kwhConsumption)
        customers.append(customerCount)
        kwdCon.append(kwdConsumption)
    sum_meterConsumption = sum(meterConsumption)
    sum_customerCount = sum(customers)
    sum_kwdConsumption = sum(kwdCon)
    if sum_customerCount > 0:
        cf = getCF(sum_customerCount)
        kva = cf * sum_kwdConsumption
    print(f'txGUID:{_GID}{nl}{t}{svcPntCount} meters related{nl}{t}{sum_customerCount} customers{nl}{t}total kwh: {sum_meterConsumption}{nl}{t}total kwd: {sum_kwdConsumption}{nl}{t}CF:{cf}{nl}{t}Recommended KVA:{kva} ')
    #return sum(sum_kwhConsumption)

In [37]:
def getConsumption(svcPntGUID): 
    kwh = []
    kwd = []
    with arcpy.da.SearchCursor(custAcctDest,custAcctFlds,f"eServicePoint_GlobalID = '{svcPntGUID}'") as custAccts:
        for custAcct in custAccts:
            kwh.append(custAcct[1])
            KWD = getKWD(custAcct[1])
            if KWD is None:
                KWD = calcKWD((custAcct[1]))
                kwd.append(KWD)
            else:
                kwd.append(KWD)
    #print(f'kwh: {kwh}')
    #print(f'kwd: {kwd}')
    lenKWH = len(kwh)
    sumKWH = sum(kwh)
    sumKWD = sum(kwd)
    #print(f'sum of kwh: {sumKWH}')
    #print(f'length of kwh.append: {lenKWH}')
    #print(f'sum of kwd: {sumKWD}')
    return sumKWH,lenKWH,sumKWD

In [7]:
def updateTx(OID,GID,phase,consumption):
    viewTbl = "tcview"+str(OID)
    txCon = []
    txSum = 0
    arcpy.MakeTableView_management(txDest,viewTbl,where_clause=f"GLOBALID = '{GID}'",workspace=gdb)
    if int(arcpy.GetCount_management(viewTbl).getOutput(0)) == 1:
        with arcpy.da.UpdateCursor(txDest,txFlds,f"GLOBALID = '{GID}'") as txPnts:
            #print(f'eTransformerBank_GLOBALID = "{txGUID}"')
            for txPnt in txPnts:
                #print(f'svcPntGUID {svcPnt[0]}')
                if phase == 1: # c phase [7]
                    txCon.append(txPnt[7])
                    txCon.append(consumption)
                    txPnt[7] = sum(txCon)
                if phase == 2: # b phase [6]
                    txCon.append(txPnt[6])
                    txCon.append(consumption)
                    txPnt[6] = sum(txCon)
                if phase == 3: # bc phase [6][7]
                    txCon.append(txPnt[6])
                    txCon.append(consumption/2)
                    txPnt[6] = sum(txCon)
                    txCon = []
                    txCon.append(txPnt[7])
                    txCon.append(consumption/2)
                    txPnt[7] = sum(txCon)
                if phase == 4: # a phase [5]
                    txCon.append(txPnt[5])
                    txCon.append(consumption)
                    txPnt[5] = sum(txCon)
                if phase == 5: # ac phase [5][7]
                    txCon.append(txPnt[5])
                    txCon.append(consumption/2)
                    txPnt[5] = sum(txCon)
                    txCon = []
                    txCon.append(txPnt[7])
                    txCon.append(consumption/2)
                    txPnt[7] = sum(txCon)
                if phase == 6: # ab phase [5][6]
                    txCon.append(txPnt[5])
                    txCon.append(consumption/2)
                    txPnt[5] = sum(txCon)
                    txCon =[]
                    txCon.append(txPnt[6])
                    txCon.append(consumption/2)
                    txPnt[6] = sum(txCon)
                if phase == 7: # abc phase [5][6][7]
                    txCon.append(txPnt[5])
                    txCon.append(consumption/2)
                    txPnt[5] = sum(txCon)
                    txCon =[]
                    txCon.append(txPnt[6])
                    txCon.append(consumption/2)
                    txPnt[6] = sum(txCon)
                    txCon =[]
                    txCon.append(txPnt[7])
                    txCon.append(consumption/2)
                    txPnt[7] = sum(txCon)
                txPnts.updateRow(txPnt)

In [34]:
def getKWD(consumption):
    for key in sorted(estimatedDemand.keys()):
        if consumption <= key:
            #print(key, estimatedDemand[key])
            return estimatedDemand[key]
def getKWDPhase(consumption):
    for key in sorted(estimatedDemand.keys()):
        if consumption <= key:
            #print(key, estimatedDemand[key])
            return estimatedDemand[key]
#TODO verify if * is needed
def calcKWD(consumption):
    if summerPeak: 
        #print(f'Using Summer Peak')
        return 13.95+0.0025*(consumption-3000) 
    if winterPeak:
        #print(f'Using Winter Peak')
        return 18.70+0.0027*(consumption-3000)

def getCF(custCount):
    for key in sorted(cf.keys()):
        if custCount == key:
            #print(key, cf[key])
            return cf[key]
        if custCount >= 20:
            return .37

 def getCustAcct(svcPntGUID):
     count = 0
     kwd = []
     kwdSum = 0
     minimumKVA = 0
     _cf = 1
     with arcpy.da.SearchCursor(custAcctDest,custAcctFlds,f"eServicePoint_GlobalID = '{svcPntGUID}'") as custAccts:
         for custAcct in custAccts:
             if custAcct[3] is None:
                 pass
             else:
                 custAcctCount += 1
                 print(f'MaxConsumption {custAcct[3]} and count is {count}')
                 kwdVal = getKWD(custAcct[3])
                 if kwdVal is None:
                     kwdVal = calcKWD(custAcct[3])
                 kwd.append(kwdVal)
                 #if count > 1:
                 kwdSum = sum(kwd)
                 #print(f'Sum of kwd {kwdSum}')
             _cf = getCF(count)
             if kwdSum == 0:
                 pass
             elif _cf is None:
                 pass
             else:
                 minimumKVA = kwdSum*_cf
             print(f'kwdList: {kwd}')
             print(f'Sum of kwd {kwdSum}')
             print(f'_cf {_cf}')
             print(f'Estimated Load: {minimumKVA}kva')
         return kwdSum, _cf, minimumKVA
     return 0,0,0

 def getKWD(consumption):
     for key in sorted(estimatedDemand.keys()):
         if consumption <= key:
             #print(key, estimatedDemand[key])
             return estimatedDemand[key]
 def getKWDPhase(consumption):
     for key in sorted(estimatedDemand.keys()):
         if consumption <= key:
             #print(key, estimatedDemand[key])
             return estimatedDemand[key]

def calcKWD(consumption):
     if summerPeak:
         print(f'Using Summer Peak')
         return 13.95+0.0025*(consumption-3000)
     if winterPeak:
         print(f'Using Winter Peak')
         return 18.70+0.0027*(consumption-3000)

 def getCF(custCount):
     for key in sorted(cf.keys()):
         if custCount == key:
             #print(key, cf[key])
             return cf[key]
         if custCount >= 20:
             return .37

In [9]:
tblList = arcpy.ListTables()
for tbl in tblList:
    print(f'Deleting {tbl}')
    arcpy.Delete_management(tbl)
fdsList = arcpy.ListDatasets()
for fds in fdsList:
    print(f'Deleting {fds}')
    arcpy.Delete_management(fds)

Deleting eCUSTOMERACCOUNT
Deleting SAP_INSTALLATION
Deleting ServicePoint_Statistics
Deleting Electric


In [10]:
print(f'Copying custAcctSource to custAcctDest')
arcpy.Copy_management(custAcctSource,custAcctDest)
for fld in txAddFlds:
    print(f'Adding {fld} in {txDest}')
    arcpy.AddField_management(txDest,fld,"DOUBLE")

Copying custAcctSource to custAcctDest
Adding kWDSum in C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Adding CF in C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Adding kWDSumXCF in C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Adding kWDSumXCF_A in C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Adding kWDSumXCF_B in C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Adding kWDSumXCF_C in C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank


In [11]:
txMaxFlds = ["MAXCUSTOMERCONSUMPTION_A","MAXCUSTOMERCONSUMPTION_B","MAXCUSTOMERCONSUMPTION_C"]
for txMaxFld in txMaxFlds:
    print(f'Resetting {txMaxFld} in  to Zero {txDest}')
    arcpy.CalculateField_management(txDest,txMaxFld,0)
print(f'Calc MaxCustCon to Zero in svcPntDest')
arcpy.CalculateField_management(svcPntDest,"MAXCUSTOMERCONSUMPTION",0)

Resetting MAXCUSTOMERCONSUMPTION_A in  to Zero C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Resetting MAXCUSTOMERCONSUMPTION_B in  to Zero C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Resetting MAXCUSTOMERCONSUMPTION_C in  to Zero C:\Users\friendde\Documents\ArcGIS\Projects\ReplaceKVA\ReplaceKVA.gdb\Electric\eTransformerBank
Calc MaxCustCon to Zero in svcPntDest


<Result 'C:\\Users\\friendde\\Documents\\ArcGIS\\Projects\\ReplaceKVA\\ReplaceKVA.gdb\\Electric\\eServicePoint'>

In [12]:
print('Calc MaxCon to Zero if None in custAcctDest')
expression = "setZero(!MAXCONSUMPTION!)"
codeblock = """
def setZero(maxcon):
    if maxcon is None:
        return 0
    else:
        return maxcon"""
arcpy.CalculateField_management(custAcctDest,"MAXCONSUMPTION",expression,"PYTHON3",codeblock)

Calc MaxCon to Zero if None in custAcctDest


<Result 'C:\\Users\\friendde\\Documents\\ArcGIS\\Projects\\ReplaceKVA\\ReplaceKVA.gdb\\eCUSTOMERACCOUNT'>

In [13]:
edit = arcpy.da.Editor(gdb)
edit.startEditing(False, False)
edit.startOperation()

In [47]:
#with arcpy.da.UpdateCursor(txDest,txFlds,where_clause="GLOBALID = '{14341799-1A68-491E-9E13-7C619ACBAEC5}'") as txPnts:
with arcpy.da.UpdateCursor(txDest,txFlds) as txPnts:
        for txPnt in txPnts:
            count = 0 
            kwh = [] 
            kwhSum = 0
            print(f'DeviceID: {txPnt[9]} Phase:{txPnt[13]} KVA_A:{txPnt[15]} KVA_B:{txPnt[16]} KVA_C:{txPnt[17]}')
            sumSvcPnts(txPnt[0],txPnt[1])
            #kwhSum = sumSvcPnts(txPnt[0],txPnt[1])
            #print(f"kwh sum: {kwhSum}")

DeviceID: NONE1 Phase:4 KVA_A:25 KVA KVA_B:NONE KVA_C:NONE
txGUID:{AABE1886-61B0-44E6-9DF7-D505A10FFCD2}
	2 meters related
	2 customers
	total kwh: 530.0
	total kwd: 7.369999999999999
	CF:0.85
	Recommended KVA:6.264499999999999 
DeviceID: NONE2 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{D2D5169C-A715-46E0-91EE-36D01B04FC2D}
	2 meters related
	2 customers
	total kwh: 2651.0
	total kwd: 16.93
	CF:0.85
	Recommended KVA:14.3905 
DeviceID: NONE3 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{7CCCBA17-54EF-42AA-9A87-02159ACDA324}
	3 meters related
	3 customers
	total kwh: 4961.0
	total kwd: 29.009999999999998
	CF:0.74
	Recommended KVA:21.467399999999998 
DeviceID: 1978R1 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{DFDB886D-DEB4-43BC-8C61-7DBD12C22C2F}
	1 meters related
	1 customers
	total kwh: 2117.0
	total kwd: 11.26
	CF:1.0
	Recommended KVA:11.26 
DeviceID: NONE5 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{ADB0EEA9-99B5-476D-9F44-39730CB65611}
	1 meters related
	1

txGUID:{10ECAA23-EB9C-44DE-B5D2-1E4B352E9C57}
	8 meters related
	7 customers
	total kwh: 9967.0
	total kwd: 60.73
	CF:0.54
	Recommended KVA:32.794200000000004 
DeviceID: 138L2 Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:25 KVA
txGUID:{19D1E915-A05F-4062-88D2-059FB3D3EB82}
	9 meters related
	9 customers
	total kwh: 12476.0
	total kwd: 77.76
	CF:0.5
	Recommended KVA:38.88 
DeviceID: NONE48 Phase:7 KVA_A:75 KVA KVA_B:75 KVA KVA_C:75 KVA
txGUID:{F035C4FB-BEC2-419E-BFEE-4D14ACBBE5BF}
	1 meters related
	1 customers
	total kwh: 4190.0
	total kwd: 16.925
	CF:1.0
	Recommended KVA:16.925 
DeviceID: 137L5 Phase:2 KVA_A:NONE KVA_B:75 KVA KVA_C:NONE
txGUID:{10848710-DB61-4C28-B56C-7633A53EE1EA}
	17 meters related
	16 customers
	total kwh: 26313.0
	total kwd: 141.82
	CF:0.41
	Recommended KVA:58.14619999999999 
DeviceID: 135L9T Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:75 KVA
txGUID:{E1F4FBF2-F74A-4543-8726-1AB3F70D9151}
	18 meters related
	17 customers
	total kwh: 27931.0
	total kwd: 161.54
	CF:0.39
	Recommended 

txGUID:{326E73C3-8BDA-4514-9465-613A15D18D87}
	1 meters related
	1 customers
	total kwh: 32520.0
	total kwd: 87.75
	CF:1.0
	Recommended KVA:87.75 
DeviceID: NONE97 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{7A86AE3E-B199-4BD5-A2A4-4110E360BF85}
	4 meters related
	4 customers
	total kwh: 7057.0
	total kwd: 40.21
	CF:0.66
	Recommended KVA:26.538600000000002 
DeviceID: NONE100 Phase:4 KVA_A:25 KVA KVA_B:NONE KVA_C:NONE
txGUID:{3419FDF4-847C-4DE8-879B-27417A92C3F4}
	1 meters related
	1 customers
	total kwh: 1726.0
	total kwd: 9.95
	CF:1.0
	Recommended KVA:9.95 
DeviceID: NONE101 Phase:4 KVA_A:25 KVA KVA_B:NONE KVA_C:NONE
txGUID:{EB522E94-A168-4397-8CFA-BE5D09A11362}
	1 meters related
	1 customers
	total kwh: 709.0
	total kwd: 5.92
	CF:1.0
	Recommended KVA:5.92 
DeviceID: 4034R1 Phase:7 KVA_A:167 KVA KVA_B:167 KVA KVA_C:167 KVA
txGUID:{DA51F244-89CD-458E-895A-ACFBA2102C7C}
	1 meters related
	1 customers
	total kwh: 55700.0
	total kwd: 145.7
	CF:1.0
	Recommended KVA:145.7 
DeviceID: 

	Recommended KVA:34.045 
DeviceID: NONE170 Phase:4 KVA_A:25 KVA KVA_B:NONE KVA_C:NONE
txGUID:{FFACBBB1-C96F-4AF2-AE91-7AB6318F78A2}
	3 meters related
	3 customers
	total kwh: 4418.0
	total kwd: 26.17
	CF:0.74
	Recommended KVA:19.3658 
DeviceID: 1008R1 Phase:4 KVA_A:25 KVA KVA_B:NONE KVA_C:NONE
txGUID:{9F8D70BE-3DAD-4242-A61C-6B3713DCDE83}
	1 meters related
	1 customers
	total kwh: 3653.0
	total kwd: 15.5825
	CF:1.0
	Recommended KVA:15.5825 
DeviceID: NONE172 Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:50 KVA
txGUID:{641BCE75-AB79-4AA1-9577-0075B6E71FFA}
	8 meters related
	8 customers
	total kwh: 15154.0
	total kwd: 73.0175
	CF:0.52
	Recommended KVA:37.9691 
DeviceID: NONE173 Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:50 KVA
txGUID:{2946F730-3EF5-4225-94DE-48F217490405}
	10 meters related
	10 customers
	total kwh: 26051.0
	total kwd: 117.96
	CF:0.49
	Recommended KVA:57.800399999999996 
DeviceID: NONE174 Phase:4 KVA_A:50 KVA KVA_B:NONE KVA_C:NONE
txGUID:{8574DBF4-43FC-4674-A98B-898171494CCF}
	3 meters 

txGUID:{8D41837D-E4B9-4B92-A5FD-B25D4B261C41}
	1 meters related
	1 customers
	total kwh: 937.0
	total kwd: 6.82
	CF:1.0
	Recommended KVA:6.82 
DeviceID: NONE215 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{AE4A6F58-9CC6-4CDF-ADA0-951C18AAEF91}
	1 meters related
	1 customers
	total kwh: 188.0
	total kwd: 3.2
	CF:1.0
	Recommended KVA:3.2 
DeviceID: NONE216 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{16BD8E7D-6080-4417-B846-BC10CAFD8863}
	1 meters related
	1 customers
	total kwh: 793.0
	total kwd: 6.15
	CF:1.0
	Recommended KVA:6.15 
DeviceID: NONE217 Phase:4 KVA_A:25 KVA KVA_B:NONE KVA_C:NONE
txGUID:{997EDD87-8728-4A86-BD45-594FA4808BA3}
	3 meters related
	2 customers
	total kwh: 3217.0
	total kwd: 8.28
	CF:0.85
	Recommended KVA:7.037999999999999 
DeviceID: NONE218 Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:25 KVA
txGUID:{21FBEB5C-A18D-4B31-87E6-6544761D1CFE}
	2 meters related
	1 customers
	total kwh: 0.0
	total kwd: 2.4
	CF:1.0
	Recommended KVA:2.4 
DeviceID: NONE219 Phase:2 KVA_A:

...

txGUID:{5CBB5E70-9106-49B4-8CAA-884D638D42EA}
	1 meters related
	1 customers
	total kwh: 3342.0
	total kwd: 14.805
	CF:1.0
	Recommended KVA:14.805 
DeviceID: NONE254974 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{0B916CE8-3E8D-40BB-A2FE-B4B2D68356DE}
	1 meters related
	1 customers
	total kwh: 44.0
	total kwd: 2.4
	CF:1.0
	Recommended KVA:2.4 
DeviceID: 4504L4 Phase:4 KVA_A:100 KVA KVA_B:NONE KVA_C:NONE
txGUID:{5C6BB7B3-E711-4F74-A245-B4163CABD5CB}
	3 meters related
	21 customers
	total kwh: 32043.0
	total kwd: 186.0425
	CF:0.37
	Recommended KVA:68.835725 
DeviceID: 4504L3 Phase:4 KVA_A:100 KVA KVA_B:NONE KVA_C:NONE
txGUID:{BDB884C3-47CE-4132-B537-2BA099894C07}
	2 meters related
	20 customers
	total kwh: 29228.0
	total kwd: 176.56
	CF:0.37
	Recommended KVA:65.3272 
DeviceID: 4504L2 Phase:4 KVA_A:100 KVA KVA_B:NONE KVA_C:NONE
txGUID:{D08F2A28-B083-4DEF-9DC6-6464CD1AEF92}
	2 meters related
	16 customers
	total kwh: 26387.0
	total kwd: 143.18
	CF:0.41
	Recommended KVA:58.7038 
Devic

DeviceID: NONE302167 Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:25 KVA
txGUID:{71671283-2702-4AC5-B4A3-7BD8398C3BD2}
	1 meters related
	1 customers
	total kwh: 1598.0
	total kwd: 9.42
	CF:1.0
	Recommended KVA:9.42 
DeviceID: NONE302567 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{F6F37350-677A-4B70-A0A4-284F4D10B2AD}
	1 meters related
	1 customers
	total kwh: 2.0
	total kwd: 2.4
	CF:1.0
	Recommended KVA:2.4 
DeviceID: 4579R2 Phase:7 KVA_A:167 KVA KVA_B:167 KVA KVA_C:167 KVA
txGUID:{817F5223-4BA8-4FC2-B81C-4D5F49AE0BB4}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: NONE302968 Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:37.5 KVA
txGUID:{26B26E95-A4DA-462B-8FB9-E6150B47081B}
	2 meters related
	2 customers
	total kwh: 4898.0
	total kwd: 24.57
	CF:0.85
	Recommended KVA:20.8845 
DeviceID: NONE302969 Phase:2 KVA_A:NONE KVA_B:25 KVA KVA_C:NONE
txGUID:{E699B6CB-F045-4C90-953C-C84A25EE49B5}
	1 meters related
	1 customers
	total kwh: 1330.0
	total kwd: 8.48

txGUID:{4383A6DC-AA55-4990-A23F-8619A865A3BC}
	2 meters related
	2 customers
	total kwh: 1754.0
	total kwd: 12.45
	CF:0.85
	Recommended KVA:10.5825 
DeviceID: 621L13 Phase:2 KVA_A:NONE KVA_B:50 KVA KVA_C:NONE
txGUID:{B577D372-A0D4-4B2C-9D9E-714953E63FB8}
	1 meters related
	1 customers
	total kwh: 1710.0
	total kwd: 9.95
	CF:1.0
	Recommended KVA:9.95 
DeviceID: 4634R1 Phase:7 KVA_A:167 KVA KVA_B:167 KVA KVA_C:167 KVA
txGUID:{576C92F2-DCFF-4863-BD80-6696A21F448E}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: 4641L2 Phase:2 KVA_A:NONE KVA_B:50 KVA KVA_C:NONE
txGUID:{D8E7186E-ABBA-4074-89A5-56A601735C8B}
	1 meters related
	1 customers
	total kwh: 217.0
	total kwd: 3.46
	CF:1.0
	Recommended KVA:3.46 
DeviceID: NONE345468 Phase:7 KVA_A:100 KVA KVA_B:100 KVA KVA_C:100 KVA
txGUID:{407154FE-006D-4F38-AA0F-19BC3979999D}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: 923L3 Phase:7 KVA_A:37.5 KVA KVA_B

	Recommended KVA:16.557999999999996 
DeviceID: 4662L9 Phase:1 KVA_A:NONE KVA_B:NONE KVA_C:100 KVA
txGUID:{B79BDE90-CE12-418B-89E7-E86802892F5F}
	4 meters related
	9 customers
	total kwh: 15737.0
	total kwd: 78.62
	CF:0.5
	Recommended KVA:39.31 
DeviceID: 3721L7 Phase:7 KVA_A:100 KVA KVA_B:100 KVA KVA_C:100 KVA
txGUID:{87545816-1CE5-422D-9AAA-5C9B56543F1E}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: 4666L4 Phase:7 KVA_A:75 KVA KVA_B:75 KVA KVA_C:75 KVA
txGUID:{9CABD9EA-748C-4900-907E-3BCBCCEDE6CA}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: 4666L1 Phase:7 KVA_A:100 KVA KVA_B:100 KVA KVA_C:100 KVA
txGUID:{70C612FA-000F-466E-A5E7-C4FD1EB7E979}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: 4665L3 Phase:7 KVA_A:167 KVA KVA_B:167 KVA KVA_C:167 KVA
txGUID:{C47E65EE-8103-45D5-BDEF-5A3A5EDB7946}
	1 meters related
	0 customers
	total kwh: 0
	total

txGUID:{6D52A2E6-9C57-4C3C-920D-6E8C01AF867D}
	3 meters related
	3 customers
	total kwh: 6433.0
	total kwd: 33.4
	CF:0.74
	Recommended KVA:24.715999999999998 
DeviceID: 4702R2 Phase:7 KVA_A:167 KVA KVA_B:167 KVA KVA_C:167 KVA
txGUID:{E6547392-2162-4FA1-A284-4F51B07780D6}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: None Phase:7 KVA_A:100 KVA KVA_B:100 KVA KVA_C:100 KVA
txGUID:{EE3953E5-1033-41A0-81D9-E0785E8B2F51}
	1 meters related
	36 customers
	total kwh: 0.0
	total kwd: 86.40000000000003
	CF:0.37
	Recommended KVA:31.96800000000001 
DeviceID: None Phase:7 KVA_A:167 KVA KVA_B:167 KVA KVA_C:167 KVA
txGUID:{286F5AFD-1A9D-4017-AC79-AAFFFD2F3335}
	0 meters related
	0 customers
	total kwh: 0
	total kwd: 0
	CF:0
	Recommended KVA:0 
DeviceID: 4180L5 Phase:7 KVA_A:100 KVA KVA_B:100 KVA KVA_C:100 KVA
txGUID:{C5AC526B-9708-4709-A567-82743FF6D520}
	1 meters related
	1 customers
	total kwh: 0.0
	total kwd: 2.4
	CF:1.0
	Recommended KVA:2.4 


In [48]:
edit.stopOperation()
edit.stopEditing(True)


# ### Use numpy and pandas to export to CSV
# 
# Use arcpy [```TableToNumPyArray()```](http://pro.arcgis.com/en/pro-app/arcpy/data-access/tabletonumpyarray.htm)
# See also [Working with numpy in ArcGIS](http://pro.arcgis.com/en/pro-app/arcpy/get-started/working-with-numpy-in-arcgis.htm)

# nparr = arcpy.da.TableToNumPyArray(custAcctDest,custAcctOutFlds,skip_nulls=True)
# #nparr = arcpy.da.TableToNumPyArray(custAcctDest,custAcctOutFlds,null_value=-9999)
# pdarr = pd.DataFrame(nparr)
# pdarr.to_csv(custAcctFile,header=False, index=False)

# TODO - write file to \\gruadmin.gru.com\fs\Groups\OMS Replacement Project\Documents for OSII\Customer and Premise Files

# Ready new numpy array for consumption analysis

# nparr = arcpy.da.TableToNumPyArray(custAcctDest,["SERVICEPOINTOBJECTID","POINT_X","POINT_Y","AVGCONSUMPTION","MAXCONSUMPTION"],skip_nulls=True)

# df = pd.DataFrame(nparr)
# df.head()

# [```gis.features.SpatialDataFrame()```](https://esri.github.io/arcgis-python-api/apidoc/html/arcgis.features.toc.html?highlight=spatialdataframe#arcgis.features.SpatialDataFrame.from_xy)

# from arcgis.features import SpatialDataFrame
# from arcgis.gis import GIS
# from getpass import getpass
# from IPython.display import display

# sdf = SpatialDataFrame.from_xy(df,"POINT_X","POINT_Y")
# gis = GIS(arcpy.GetActivePortalURL(), username=input("Enter User Name "), password=(getpass()))
# #gis = GIS()
# #portalDesc = arcpy.GetPortalDescription()
# # search and list all items owned by connected user
# #query=f'owner:{portalDesc["user"]["username"]} AND title:CW BaseMap'
# #itemType="Feature Layer"
# #sortField="title"
# #sortOrder="asc"
# # default max__items is 10
# #maxItems=100
# #m = gis.content.search(query,itemType,sortField,sortOrder,maxItems)

# #consumptionLyr = gis.content.import_data(sdf)

# m = gis.map('Gainesville,FL')

# m.add_layer(sdf,options={"renderer":"ClassedSizeRenderer","field_name":"MAXCONSUMPTION"})

# #m.add_layer(consumptionLyr,options={"renderer":"ClassedSizeRenderer","field_name":"MAXCONSUMPTION"})

# m
